In [1]:
import pandas as pd
import numpy as np

In [2]:
from gp_pref_elicit_luisa import gaussian_process as GP 
from gp_pref_elicit_luisa import dataset as data 
from gp_pref_elicit_luisa import acquisition_function as acquisition_function
from gp_pref_elicit_luisa.gp_utilities import utils_ccs as gp_utils_ccs
from gp_pref_elicit_luisa.gp_utilities import utils_data as gp_utils_data
from gp_pref_elicit_luisa.gp_utilities import utils_user as gp_utils_users

In [3]:
# gp_utils_ccs.get_ccs(2, 20)
# outputs a synthetic Pareto Coverage Set of value vectors with 2 objectives and 20 datapoints

The original dataset, in the data_preprocessed.ipynb file, can not be used for the Gaussian Process as it is not in the form of value vectors. To bring it into the form of value vectors, the dataset needs to be passed into a Multi-Objective Shortest Path Planning Solver which will output value vectors. These value vectors can then be an input for the GP. Thus, for now, I am using a synthetic Pareto Coverage Set (PCS) with 2 objectives and 20 datapoints which gives us synthetic value vectors for input to the GP.

In [4]:
synthetic_pcs = np.array([[0.08354893, 0.99771414],
       [0.17329006, 0.98281369],
       [0.93898169, 0.37256163],
       [0.57360241, 0.848919  ],
       [0.98568813, 0.18298825],
       [0.11718526, 0.99496982],
       [0.69436633, 0.7426556 ],
       [0.419793  , 0.90681482],
       [0.99850198, 0.05548771],
       [0.97244122, 0.25252888],
       [0.97837106, 0.22331134],
       [0.21266473, 0.97269664],
       [0.8964366 , 0.49411589],
       [0.25476081, 0.96052451],
       [1.        , 0.        ],
       [0.35559809, 0.92879935],
       [0.80235668, 0.62389126],
       [0.        , 1.        ],
       [0.27334299, 0.95488636],
       [0.99132009, 0.1452147 ]])
synthetic_pcs 

array([[0.08354893, 0.99771414],
       [0.17329006, 0.98281369],
       [0.93898169, 0.37256163],
       [0.57360241, 0.848919  ],
       [0.98568813, 0.18298825],
       [0.11718526, 0.99496982],
       [0.69436633, 0.7426556 ],
       [0.419793  , 0.90681482],
       [0.99850198, 0.05548771],
       [0.97244122, 0.25252888],
       [0.97837106, 0.22331134],
       [0.21266473, 0.97269664],
       [0.8964366 , 0.49411589],
       [0.25476081, 0.96052451],
       [1.        , 0.        ],
       [0.35559809, 0.92879935],
       [0.80235668, 0.62389126],
       [0.        , 1.        ],
       [0.27334299, 0.95488636],
       [0.99132009, 0.1452147 ]])

In [5]:
# initializing GP, Dataset and Acquisition Function 
# num_objectives = 2
GP = GP.GPPairwise(num_objectives=2)
utils_comparisons = data.DatasetPairwise(num_objectives=2)
acquisition_function_DA = acquisition_function.DiscreteAcquirer(input_domain=synthetic_pcs, query_type='pairwise', seed=None, acquisition_type='expected improvement')
acquisition_function_EI = acquisition_function.get_expected_improvement(datapoints=synthetic_pcs, gaussian_process=GP, datapoints_hist=acquisition_function_DA.history, xi=0.01)

In [6]:
# getting the user preferences for generating a ground truth utility function
user_pref = gp_utils_users.UserPreference(num_objectives=2, std_noise=0.1)

In [7]:
# getting the datapoints at which we need to query the user first 
start_points = acquisition_function_DA.get_start_points(gaussian_process=GP)
start_points


(array([0.08354893, 0.99771414]), array([0.80235668, 0.62389126]))

In [8]:
# generating utilities for the starting datapoints
ground_truth_utility_func = user_pref.get_preference(start_points, add_noise=True)
ground_truth_utility_func

array([0.07042117, 0.9023785 ])

In [9]:
# ground_truth_utility_func = user_pref.get_preference(synthetic_pcs, add_noise=True)
# ground_truth_utility_func

In [10]:
highest_utility_index = np.argmax(ground_truth_utility_func)
lowest_utility_index = np.argmin(ground_truth_utility_func)
print('Highest utility is at index ', highest_utility_index,  'for the user in the dataset', '\n', 
'Lowest utility is at index ', lowest_utility_index, 'for the user in the dataset')
# this outputs the index of the points in the synthetic dataset which have the highest and lowest utility

Highest utility is at index  1 for the user in the dataset 
 Lowest utility is at index  0 for the user in the dataset


In [32]:
highest_utility_point_dataset = start_points[highest_utility_index]
lowest_utility_point_dataset = start_points[lowest_utility_index]
print('highest_point:', highest_utility_point_dataset, '\n',
      'lowest point: ', lowest_utility_point_dataset)

highest_point: [0.80235668 0.62389126] 
 lowest point:  [0.8964366  0.49411589]


In [11]:
# getting the user preference for the datapoint in the synthetic dataset having the highest utility
# ground_truth_utility_func = user_pref.get_preference(synthetic_pcs[highest_utility_index], add_noise=True)
# ground_truth_utility_func

In [34]:
# comparing datapoints with highest and lowest utility values generated from the ground truth utility function 
# and adding these to the GP
utils_comparisons.add_single_comparison(highest_utility_point_dataset, lowest_utility_point_dataset)
utils_comparisons_datapoints_start = utils_comparisons.datapoints
utils_comparisons_datapoints_start

array([[0.17329006, 0.98281369],
       [0.08354893, 0.99771414],
       [0.57360241, 0.848919  ],
       [0.80235668, 0.62389126],
       [0.8964366 , 0.49411589]])

In [40]:
# to get the point which will be retained by the comparison in the dataset
highest_point = np.argmax(utils_comparisons_datapoints_start)
highest_point_datapoint = utils_comparisons_datapoints_start[highest_point]
current_max_points = np.array([highest_point_datapoint])
current_max_points

array([[0.80235668, 0.62389126]])

In [14]:
# updating the GP based on the comparisons added to the dataset
GP.update(utils_comparisons)

In [15]:
# gives the next points to query for the user 
next_points = acquisition_function_DA.get_next_point(gaussian_process=GP, dataset=utils_comparisons)
next_points
# outputs next set of value vectors for comparisons

array([0.57360241, 0.848919  ])

In [16]:
# we now run the user preference on the next points to query
ground_truth_utility_func = user_pref.get_preference(x=next_points, add_noise=True)
ground_truth_utility_func

array([0.76002569])

In [17]:
# we get the index of the highes point which indicates highest utility for the datapoint
highest_utility_index1 = np.argmax(ground_truth_utility_func)
highest_utility_index1

0

In [42]:
highest_utility_point_dataset2 = next_points[highest_utility_index1]
# lowest_utility_point_dataset = start_points[lowest_utility_index]
print('highest_point:', highest_utility_point_dataset2, '\n')
    #   'lowest point: ', lowest_utility_point_dataset)

highest_point: 0.8964366 



In [43]:
# comparing datapoints with highest and lowest utility values generated from the ground truth utility function 
# and adding these to the GP
utils_comparisons_next = utils_comparisons.add_single_comparison(current_max_points, highest_utility_point_dataset2)
utils_comparisons_datapoints_next = utils_comparisons.datapoints
utils_comparisons_datapoints_next 

array([[0.17329006, 0.98281369],
       [0.08354893, 0.99771414],
       [0.57360241, 0.848919  ],
       [0.80235668, 0.62389126],
       [0.8964366 , 0.49411589],
       [0.8964366 , 0.8964366 ]])

In [44]:
# to get the point which will be retained by the comparison in the dataset
highest_point1 = np.argmax(utils_comparisons_datapoints_next)
highest_point_datapoint1 = utils_comparisons_datapoints_next[highest_point1]
current_max_points = np.array([highest_point_datapoint1])
current_max_points

array([[0.80235668, 0.62389126]])

In [19]:
GP.update(utils_comparisons)

In [20]:
# points to exclude for getting the expected improvement
# we do this because we want to exclude all the points the current maximum was already compared to
exclude = acquisition_function.exclude_points_pairwise(dataset=utils_comparisons)
exclude

array([[0.57360241, 0.848919  ],
       [0.08354893, 0.99771414]])

In [21]:
next_point_EI = acquisition_function_DA.get_next_point_EI(gaussian_process=GP, exclude=exclude)
next_point_EI

array([0.8964366 , 0.49411589])

In [22]:
# generating utilities for the next datapoints according to EI
ground_truth_utility_func1 = user_pref.get_preference(next_point_EI, add_noise=True)
ground_truth_utility_func1

array([0.93186318])

In [23]:
# we get the index of the highes point which indicates highest utility for the datapoint
highest_utility_index2 = np.argmax(ground_truth_utility_func1)
highest_utility_index2

0

In [24]:
# comparing datapoints with highest and lowest utility values generated from the ground truth utility function 
# and adding these to the GP
utils_comparisons.add_single_comparison(synthetic_pcs[highest_point], synthetic_pcs[highest_utility_index1])
utils_comparisons_datapoints = utils_comparisons.datapoints
utils_comparisons_datapoints 

array([[0.17329006, 0.98281369],
       [0.08354893, 0.99771414],
       [0.57360241, 0.848919  ]])

In [25]:
GP.update(utils_comparisons)

In [26]:
# similarly for this, I am not sure if the input and output are correct
acquisition_function.get_expected_improvement(datapoints=synthetic_pcs, gaussian_process=GP, datapoints_hist=acquisition_function_DA.history, xi=0.01)

array([0.10874474, 0.13278179, 0.24197855, 0.13514941, 0.24197613,
       0.12633909, 0.20897778, 0.21909455, 0.24197612, 0.2419762 ,
       0.24197615, 0.12804089, 0.24201602, 0.1354714 , 0.24197612,
       0.20872852, 0.24151192, 0.08109925, 0.14549412, 0.24197612])

In [27]:
prob_impr = acquisition_function.get_probability_of_improvement(x=next_point_EI, gaussian_process=GP, x_previous=start_points)
prob_impr

array([0.48313571])

In [11]:
# starting points in the dataset
start_points = acquisition_function_DA.get_start_points(gaussian_process=GP) 
# generating ground truth utility function for the starting points
ground_truth_utility_function_start = user_pref.get_preference(start_points, add_noise=True)
# getting the index of the highest utility
highest_utility_index_start = np.argmax(ground_truth_utility_function_start)
# getting the index of the lowest utility
lowest_utility_index_start = np.argmin(ground_truth_utility_function_start)
# mapping the indices of the highest utility to the actual datapoint in the dataset
highest_utility_point_dataset = start_points[highest_utility_index_start]
# mapping the indices of the lowest utility to the actual datapoint in the dataset
lowest_utility_point_dataset = start_points[lowest_utility_index_start]

# adding the highest utility point, which is the winner, to the dataset 
utils_comparisons.add_single_comparison(highest_utility_point_dataset, lowest_utility_point_dataset)
# computing the datapoints for this comparisons dataset
utility_comparisons_datapoints_start = utils_comparisons.datapoints

# getting the index of the highest point in utils comparison dataset
highest_point = np.argmax(utility_comparisons_datapoints_start)
# mapping the index to the dataset
highest_point_datapoint = utility_comparisons_datapoints_start[highest_point]

# adding the actual point to the array 
current_max_points = np.array([highest_point_datapoint])

# updating the GP
GP.update(utils_comparisons)

# checking which points to exclude
exclude_points = acquisition_function.exclude_points_pairwise(dataset=utils_comparisons)

print('Start points: ', start_points, '\n',
      'Point in the dataset having highest utility: ', highest_utility_point_dataset, '\n',
      'Point in the dataset having lowest utility: ', lowest_utility_point_dataset, '\n',
      'Comparison dataset datapoints: ', utility_comparisons_datapoints_start, '\n',
      'Index of the highest point in the comparisons dataset: ', highest_point, '\n',
      'The point which will be retained: ', highest_point_datapoint, '\n',
      'Current max: ', current_max_points, '\n', 
      'Excluded points: ', exclude_points)

Start points:  (array([0.69436633, 0.7426556 ]), array([0.57360241, 0.848919  ])) 
 Point in the dataset having highest utility:  [0.69436633 0.7426556 ] 
 Point in the dataset having lowest utility:  [0.57360241 0.848919  ] 
 Comparison dataset datapoints:  [[1.         0.        ]
 [0.98568813 0.18298825]
 [0.93898169 0.37256163]
 [0.97837106 0.22331134]
 [0.69436633 0.7426556 ]
 [0.57360241 0.848919  ]] 
 Index of the highest point in the comparisons dataset:  0 
 The point which will be retained:  [1. 0.] 
 Current max:  [[1. 0.]] 
 Excluded points:  [[0.69436633 0.7426556 ]
 [0.57360241 0.848919  ]]


In [67]:
# next points in the dataset according to Expected Improvement
next_point_EI = acquisition_function_DA.get_next_point_EI(gaussian_process=GP, exclude=exclude_points) 
# generating ground truth utility function for the next points
ground_truth_utility_function_next_EI = user_pref.get_preference(next_point_EI, add_noise=True)
# getting the index of the highest utility
highest_utility_index_next_EI = np.argmax(ground_truth_utility_function_next_EI)
# getting the index of the lowest utility
# lowest_utility_index_next_EI = np.argmin(ground_truth_utility_function_next_EI)
# mapping the indices of the highest utility to the actual datapoint in the dataset
highest_utility_point_next_EI = next_point_EI[highest_utility_index_next_EI]
# mapping the indices of the lowest utility to the actual datapoint in the dataset
# lowest_utility_point_dataset = next[lowest_utility_index]

# adding the highest utility point, which is the winner, to the dataset 
utils_comparisons.add_single_comparison(current_max_points, highest_utility_point_next_EI)
# computing the datapoints for this comparisons dataset
utility_comparisons_datapoints_next_EI = utils_comparisons.datapoints

# calculating the highest combination of values
combined_datapoint_next_EI_sum = np.sum(utility_comparisons_datapoints_next_EI, axis=1)
# # getting the index of the highest point in utils comparison dataset
highest_point_next_EI = np.argmax(combined_datapoint_next_EI_sum)
# mapping the index to the dataset
highest_point_datapoint_EI = utility_comparisons_datapoints_next_EI[highest_point_next_EI]

# adding the actual point to the array 
current_max_points = np.array([highest_point_datapoint_EI])

# updating the GP
GP.update(utils_comparisons)

# checking which points to exclude
exclude_points = acquisition_function.exclude_points_pairwise(dataset=utils_comparisons)

prob_imprv = acquisition_function.get_probability_of_improvement(x=next_point_EI, gaussian_process=GP, x_previous=current_max_points)

print('next points for the GP acc to EI: ', next_point_EI, '\n',
    'Point in the dataset having highest utility: ', highest_utility_point_next_EI, '\n',
    'Comparison dataset datapoints: ', utility_comparisons_datapoints_next_EI, '\n',
    'Index of highest point in the comparisons dataset: ', highest_point_next_EI, '\n',
    'The point which will be retained: ', highest_point_datapoint_EI, '\n',
    'Current max: ', current_max_points, '\n', 
    'Excluded points: ', exclude_points, '\n',
    'Probability of improvement: ', prob_imprv)

next points for the GP acc to EI:  [1. 0.] 
 Point in the dataset having highest utility:  1.0 
 Comparison dataset datapoints:  [[0.17329006 0.98281369]
 [0.08354893 0.99771414]
 [0.57360241 0.848919  ]
 [0.80235668 0.62389126]
 [0.8964366  0.49411589]
 [0.8964366  0.8964366 ]
 [0.99850198 0.05548771]
 [1.         0.        ]
 [0.90681482 0.90681482]
 [1.         1.        ]] 
 Index of highest point in the comparisons dataset:  9 
 The point which will be retained:  [1. 1.] 
 Current max:  [[1. 1.]] 
 Excluded points:  [[1.         1.        ]
 [0.80235668 0.62389126]
 [1.         1.        ]] 
 Probability of improvement:  [0.50326204]


In [70]:
threshold = 0.45
stop_condition = False

while not stop_condition:
  # next points in the dataset according to Expected Improvement
  next_point_EI = acquisition_function_DA.get_next_point_EI(gaussian_process=GP, exclude=exclude_points) 
  # generating ground truth utility function for the next points
  ground_truth_utility_function_next_EI = user_pref.get_preference(next_point_EI, add_noise=True)
  # getting the index of the highest utility
  highest_utility_index_next_EI = np.argmax(ground_truth_utility_function_next_EI)
  # getting the index of the lowest utility
  lowest_utility_index_next_EI = np.argmin(ground_truth_utility_function_next_EI)
  # mapping the indices of the highest utility to the actual datapoint in the dataset
  highest_utility_point_next_EI = next_point_EI[highest_utility_index]
  # mapping the indices of the lowest utility to the actual datapoint in the dataset
  # lowest_utility_point_dataset = next[lowest_utility_index]

  # adding the highest utility point, which is the winner, to the dataset 
  utils_comparisons.add_single_comparison(current_max_points, highest_utility_point_next_EI)
  # computing the datapoints for this comparisons dataset
  utility_comparisons_datapoints_next_EI = utils_comparisons.datapoints

  # calculating the highest combination of values
  combined_datapoint_next_EI_sum = np.sum(utility_comparisons_datapoints_next_EI, axis=1)
  # getting the index of the highest point from the combination of values
  highest_point_next_EI = np.argmax(combined_datapoint_next_EI_sum)
  # mapping the index to the dataset
  highest_point_datapoint_EI = utility_comparisons_datapoints_next_EI[highest_point_next_EI]

  # adding the actual point to the array 
  current_max_points = np.array([highest_point_datapoint_EI])

  # updating the GP
  GP.update(utils_comparisons)

  # checking which points to exclude
  exclude_points = acquisition_function.exclude_points_pairwise(dataset=utils_comparisons)


  prob_imprv = acquisition_function.get_probability_of_improvement(x=next_point_EI, gaussian_process=GP, x_previous=current_max_points)

  print('next points for the GP acc to EI: ', next_point_EI, '\n',
    'Point in the dataset having highest utility: ', highest_utility_point_next_EI, '\n',
    'Comparison dataset datapoints: ', utility_comparisons_datapoints_next_EI, '\n',
    'Index of the highest point from the datapoints: ', highest_point_next_EI, '\n',
    'The point which will be retained: ', highest_point_datapoint_EI, '\n',
    'Current max: ', current_max_points, '\n', 
    'Excluded points: ', exclude_points, '\n',
    'Probability of improvement: ', prob_imprv)
  if prob_imprv < threshold:
    stop_condition = True

next points for the GP acc to EI:  [1. 0.] 
 Point in the dataset having highest utility:  0.0 
 Comparison dataset datapoints:  [[0.17329006 0.98281369]
 [0.08354893 0.99771414]
 [0.57360241 0.848919  ]
 [0.80235668 0.62389126]
 [0.8964366  0.49411589]
 [0.8964366  0.8964366 ]
 [0.99850198 0.05548771]
 [1.         0.        ]
 [0.90681482 0.90681482]
 [1.         1.        ]
 [0.         0.        ]] 
 Index of the highest point from the datapoints:  9 
 The point which will be retained:  [1. 1.] 
 Current max:  [[1. 1.]] 
 Excluded points:  [[1.         1.        ]
 [0.80235668 0.62389126]
 [1.         1.        ]
 [0.         0.        ]] 
 Probability of improvement:  [0.48887473]
next points for the GP acc to EI:  [1. 0.] 
 Point in the dataset having highest utility:  0.0 
 Comparison dataset datapoints:  [[0.17329006 0.98281369]
 [0.08354893 0.99771414]
 [0.57360241 0.848919  ]
 [0.80235668 0.62389126]
 [0.8964366  0.49411589]
 [0.8964366  0.8964366 ]
 [0.99850198 0.05548771]
 [

KeyboardInterrupt: 

In [ ]:
# # I haven't updated this for loop according to the code above. Once I know the code above is correct, I will put everything here
# num_iter = 2
# for i in range(num_iter):
#     # sampling on synthetic pcs according to gaussian process
#     sampled_points_GP = GP.sample(synthetic_pcs)
#     # output of this sampling is the utility values

#     # Getting highest and lowest utility values from the sampled points
#     highest_util = max(sampled_points_GP)
#     lowest_util = min(sampled_points_GP)

#     # performing single comparisons on the highest and lowest utility values
    
# print('Sampled points from the GP are: \n', sampled_points_GP, '\n' 
#     'Highest utility value is: ', highest_util, '\n'
#     'Lowest utility value is: ', lowest_util, '\n')